In [25]:
import random
import seaborn as sns

sns.set()
random.seed(42)

### Read and parse newer metadata

In [5]:
import pandas as pd

In [6]:
metadata_new = pd.read_excel('./data/metadata.xlsx')
metadata_new.drop(columns=['Unnamed: 0', '#id', 'compare_class',
       '#months', 'dateOfAdministration', '#firstName', 'class',
       '1HPSQC', '2HPSQC', '3HPSQC', '4HPSQC', '5HPSQC', '6HPSQC', '7HPSQC',
       '8HPSQC', '9HPSQC', '10HPSQC', 'jirina_ids', 'SubjectCode',
       'Overall'], inplace=True)

metadata_new.rename({'#sex': 'sex', '#DYS': 'DYS', '#age': 'age'},
                    axis=1, inplace=True)

metadata_new = metadata_new[metadata_new.DYS.notna()]  # drop NaN labels
metadata_new

filename  new_class   age  sex  DYS
0     BH1201          2   8.0  1.0  0.0
2     BH1203          2   8.0  2.0  0.0
4     BH1301          3   9.0  2.0  0.0
5     BH1302          3   9.0  1.0  0.0
6     BH1401          4  10.0  1.0  0.0
..       ...        ...   ...  ...  ...
518  TR12002          2   NaN  1.0  1.0
519  TR14004          4   NaN  2.0  1.0
520  TR14005          4   NaN  1.0  1.0
521   TR2001          0   9.0  1.0  1.0
522   BR1431          4   NaN  2.0  0.0

[459 rows x 5 columns]

In [7]:
metadata_new[metadata_new.DYS == 3]

Empty DataFrame
Columns: [filename, new_class, age, sex, DYS]
Index: []

### Read and parse the tablet data

In [8]:
import os
import re
import numpy as np

In [9]:
svcs, headers = [], []
svc_path = './data/svcs/'

for i, file in enumerate(sorted(os.listdir(svc_path))):
    file_data = np.genfromtxt(svc_path + file, skip_header=1)
    # parse the file_label and the TSK_number into groups resp.
    file_ident = re.search(r"([^_]*)_TSK([0-9]+).*", file).groups()
    headers += [file_ident[0], file_ident[1], i]
    svcs += [file_data]

svc_indexes = np.split(np.array(headers), len(headers) // 3)
svc_indexes = pd.DataFrame(svc_indexes, columns=['filename', 'tsk', 'fileindex'])

svc_indexes = svc_indexes.pivot_table('fileindex', ['filename'], 'tsk')
svc_new_data = np.array(svcs, dtype=object)
svc_indexes

tsk           10      11      12      13      14      15      16      17  \
filename                                                                   
BH1201       0.0     1.0     2.0     3.0     4.0     5.0     6.0     7.0   
BH1202      10.0    11.0    12.0    13.0    14.0    15.0    16.0    17.0   
BH1203      20.0    21.0    22.0    23.0    24.0    25.0    26.0    27.0   
BH1204      30.0    31.0    32.0    33.0    34.0    35.0    36.0    37.0   
BH1301      40.0    41.0    42.0    43.0    44.0    45.0    46.0    47.0   
...          ...     ...     ...     ...     ...     ...     ...     ...   
TR10003   4867.0  4868.0  4869.0  4870.0  4871.0  4872.0  4873.0  4874.0   
TR12002   4877.0  4878.0  4879.0  4880.0  4881.0  4882.0  4883.0  4884.0   
TR14004   4887.0  4888.0  4889.0  4890.0  4891.0  4892.0  4893.0  4894.0   
TR14005   4897.0  4898.0  4899.0  4900.0  4901.0  4902.0  4903.0  4904.0   
TR2001    4907.0  4908.0  4909.0  4910.0  4911.0  4912.0  4913.0  4914.0   

tsk            8       9  
filename                  
BH1201       8.0     9.0  
BH1202      18.0    19.0  
BH1203      28.0    29.0  
BH1204      38.0    39.0  
BH1301      48.0    49.0  
...          ...     ...  
TR10003   4875.0  4876.0  
TR12002   4885.0  4886.0  
TR14004   4895.0  4896.0  
TR14005   4905.0  4906.0  
TR2001    4915.0  4916.0  

[495 rows x 10 columns]

## Read and parse additional data

In [10]:
metadata_extra = pd.read_excel('./Dysgraphia-detection-through-machine-learning-main/data2_SciRep_pub.xlsx')
metadata_extra.drop(columns=['Unnamed: 5',  'Unnamed: 6'], inplace=True)
metadata_extra.replace({'DYSGR': 1, 'M ': 1, 'F': 2}, inplace=True)
metadata_extra.rename(columns={'diag': 'DYS'}, inplace=True)
metadata_extra

ID DYS  sex hand  age
0      6   1    2    R   15
1      7   1    1    R   15
2      8   1    1    R   14
3     11   1    1    R    8
4     13   1    1    R   14
..   ...  ..  ...  ...  ...
115  187   0    1    R   15
116  189   0    1    L   15
117  190   0    2    R   15
118  191   0    2    R   15
119  192   0    1    R   15

[120 rows x 5 columns]

In [11]:
svcs_extra, headers_extra = [], []
svc_extra_path = './Dysgraphia-detection-through-machine-learning-main/dataSciRep_public/'

for i, svc_dir in enumerate(sorted(os.listdir(svc_extra_path))):
    svc_file_dir = svc_extra_path + svc_dir + '/session00001/'
    for file in sorted(os.listdir(svc_file_dir)):
        file_data = np.genfromtxt(svc_file_dir + file, skip_header=1)
        # parse the file_label and the TSK_number into groups resp.
        file_ident = re.search(r"user(.*)", svc_dir).groups()
        headers_extra += [[file_ident[0], i]]
        svcs_extra += [file_data]
        
svc_extra_indexes = pd.DataFrame(headers_extra, columns=['ID', 'extra_fileindex'])
svc_extra_indexes.ID = svc_extra_indexes.ID.astype(int)
svc_extra_data = np.array(svcs_extra, dtype=object)
svc_extra_indexes

ID  extra_fileindex
0      6                0
1      7                1
2      8                2
3     11                3
4     13                4
..   ...              ...
115  187              115
116  189              116
117  190              117
118  191              118
119  192              119

[120 rows x 2 columns]

##### Standardize the svcs

In [12]:
svc_new_data[0][:5]

array([[6.3480e+01, 8.7000e+01, 0.0000e+00, 1.0000e+00, 5.3000e+02,
        4.8000e+02, 4.5000e+01],
       [6.3480e+01, 8.6990e+01, 7.0000e-03, 1.0000e+00, 5.3000e+02,
        4.9000e+02, 5.4000e+01],
       [6.3480e+01, 8.6975e+01, 1.5000e-02, 1.0000e+00, 5.3000e+02,
        4.9000e+02, 6.0000e+01],
       [6.3485e+01, 8.6955e+01, 2.2000e-02, 1.0000e+00, 5.3000e+02,
        4.9000e+02, 6.8000e+01],
       [6.3525e+01, 8.6930e+01, 3.0000e-02, 1.0000e+00, 5.3000e+02,
        4.9000e+02, 8.2000e+01]])

We can notice that the x, y and time values are 1000 times larger and that time is not starting at 0.

In [13]:
svc_extra_data[0][:5]

array([[1.18880000e+04, 3.21540000e+04, 7.27745086e+08, 1.00000000e+00,
        1.37000000e+03, 4.70000000e+02, 7.00000000e+00],
       [1.18880000e+04, 3.21560000e+04, 7.27745093e+08, 1.00000000e+00,
        1.37000000e+03, 4.70000000e+02, 1.80000000e+01],
       [1.18880000e+04, 3.21560000e+04, 7.27745101e+08, 1.00000000e+00,
        1.37000000e+03, 4.70000000e+02, 3.10000000e+01],
       [1.18880000e+04, 3.21570000e+04, 7.27745108e+08, 1.00000000e+00,
        1.37000000e+03, 4.70000000e+02, 4.20000000e+01],
       [1.18880000e+04, 3.21590000e+04, 7.27745116e+08, 1.00000000e+00,
        1.37000000e+03, 4.70000000e+02, 4.90000000e+01]])

In [14]:
def standardize(series):
    if len(series) == 0:
        return np.array([np.zeros(7)])
    new = series[:, :3] / 1000
    new[:, 2] = (new[:, 2] - new[0, 2]) # time starts at 0
    return np.concatenate([new, series[:, 3:]], axis=1)

In [15]:
svc_extra_data_norm = np.array([standardize(series) 
                                for series in svc_extra_data], dtype=object)

###### concatenate the two datasets

In [16]:
svc_extra_indexes.extra_fileindex += svc_new_data.shape[0]
svc_data = np.concatenate([svc_new_data, svc_extra_data_norm], axis=0)
svc_data.shape

(5037,)

In [17]:
svc_extra_indexes.head(5)

ID  extra_fileindex
0   6             4917
1   7             4918
2   8             4919
3  11             4920
4  13             4921

In [18]:
metadata_extra_merge = svc_extra_indexes.merge(metadata_extra, how='inner',
                                               on='ID')
metadata_extra_merge.drop(columns=['hand'], inplace=True)
metadata_extra_merge.rename({'extra_fileindex': 'fileindex', 'ID': 'filename'}, axis=1, inplace=True)
metadata_extra_merge

filename  fileindex DYS  sex  age
0           6       4917   1    2   15
1           7       4918   1    1   15
2           8       4919   1    1   14
3          11       4920   1    1    8
4          13       4921   1    1   14
..        ...        ...  ..  ...  ...
115       187       5032   0    1   15
116       189       5033   0    1   15
117       190       5034   0    2   15
118       191       5035   0    2   15
119       192       5036   0    1   15

[120 rows x 5 columns]

In [19]:
del svc_extra_data_norm, svc_extra_indexes

### Tablet output analysis

In [32]:
import altair as alt

In [33]:
svc_indexes = pd.DataFrame(np.split(np.array(headers), len(headers) // 3),
             columns=['filename', 'tsk', 'fileindex'])
svc_indexes.fileindex = svc_indexes.fileindex.astype(int)
svc_single = svc_indexes.merge(metadata_train, how='inner', on='filename')
svc_single.fileindex = svc_single.fileindex.astype(int)
svc_normal_10 = svc_single[(svc_single.DYS == 0) & (svc_single.tsk == '11')
          & (svc_single.age == 10)]

svc_dys_10 = svc_single[(svc_single.DYS == 1) & (svc_single.tsk == '11')
          & (svc_single.age == 10)]

svc_normal_10

filename tsk  fileindex new_class   age  sex  DYS
31     BH1401  11         61         4  10.0  1.0  0.0
41     BH1402  11         71         4  10.0  1.0  0.0
71     BH1405  11        101         4  10.0  1.0  0.0
91     BH1407  11        121         4  10.0  1.0  0.0
101    BH1408  11        131         4  10.0  1.0  0.0
111    BH1409  11        141         4  10.0  1.0  0.0
261    BR1335  11        451         3  10.0  2.0  0.0
291    BR1433  11        481         4  10.0  2.0  0.0
301    BR1434  11        491         4  10.0  2.0  0.0
351    BR3401  11        641         4  10.0  2.0  0.0
451    BR4401  11       1060         4  10.0  1.0  0.0
471    BR4404  11       1090         4  10.0  1.0  0.0
481    BR4405  11       1100         4  10.0  1.0  0.0
501    BR4407  11       1120         4  10.0  2.0  0.0
511    BR4408  11       1130         4  10.0  2.0  0.0
521    BR4409  11       1140         4  10.0  1.0  0.0
531    BR4410  11       1150         4  10.0  1.0  0.0
541    BR4412  11       1170         4  10.0  1.0  0.0
561    BR4416  11       1210         4  10.0  2.0  0.0
571    BR4417  11       1220         4  10.0  2.0  0.0
611    BR4421  11       1260         4  10.0  1.0  0.0
621    BR4423  11       1280         4  10.0  1.0  0.0
631    BR4426  11       1310         4  10.0  1.0  0.0
641    BR4428  11       1330         4  10.0  1.0  0.0
651    BR4431  11       1360         4  10.0  1.0  0.0
661    BR4432  11       1370         4  10.0  1.0  0.0
681    BR4436  11       1410         4  10.0  2.0  0.0
691    BR4437  11       1420         4  10.0  2.0  0.0
701    BR4439  11       1440         4  10.0  1.0  0.0
711    BR4441  11       1460         4  10.0  1.0  0.0
721    BR4443  11       1480         4  10.0  2.0  0.0
741    BR4445  11       1500         4  10.0  2.0  0.0
867    BR5402  11       1766         4  10.0  1.0  0.0
877    BR5403  11       1776         4  10.0  1.0  0.0
897    BR6304  11       1856         3  10.0  1.0  0.0
907    BR6402  11       1896         4  10.0  1.0  0.0
977    BR7403  11       2146         4  10.0  1.0  0.0
997    BR7405  11       2166         4  10.0  1.0  0.0
1187   HK1403  11       3973         4  10.0  2.0  0.0
1197   HK1404  11       3983         4  10.0  1.0  0.0
1207   HK1405  11       3993         4  10.0  2.0  0.0
1217   HK1406  11       4003         4  10.0  1.0  0.0
1227   HK1407  11       4013         4  10.0  1.0  0.0
1237   HK1408  11       4023         4  10.0  1.0  0.0
1247   HK1409  11       4033         4  10.0  1.0  0.0
1257   HK1410  11       4043         4  10.0  2.0  0.0
1267   HK1411  11       4053         4  10.0  2.0  0.0
1277   HK1412  11       4063         4  10.0  2.0  0.0
1297   HK1414  11       4083         4  10.0  1.0  0.0
1307   HK1415  11       4093         4  10.0  2.0  0.0
1317   HK1417  11       4113         4  10.0  1.0  0.0
1327   HK1419  11       4123         4  10.0  2.0  0.0
1337   HK1420  11       4133         4  10.0  1.0  0.0
1347   HK1421  11       4143         4  10.0  2.0  0.0
1467   HK6305  11       4508         3  10.0  1.0  0.0
1487   HK6508  11       4548         5  10.0  1.0  0.0
1497   HK6510  11       4558         5  10.0  1.0  0.0
1597   HK7302  11       4758         3  10.0  1.0  0.0

In [34]:
svc_dys_10

filename tsk  fileindex new_class   age  sex  DYS
81     BH1406  11        111         4  10.0  1.0  1.0
751    BR4446  11       1510         4  10.0  1.0  1.0
801    BR5302  11       1690         3  10.0  2.0  1.0
917    BR6501  11       1916         5  10.0  1.0  1.0
1097   BR8401  11       2316         4  10.0  1.0  1.0
1117   BR8405  11       2356         4  10.0  1.0  1.0
1167   HK1401  11       3953         4  10.0  1.0  1.0
1397    HK404  11       4350         0  10.0  2.0  1.0
1447    HK503  11       4418         0  10.0  1.0  1.0

In [4]:
def plot_drawing(x):
    to_plot = svc_data[x] - np.min(svc_data[x], axis=0)
    print(svc_data[x][2][-1])
    to_plot = pd.DataFrame(to_plot, columns=['x', 'y', 'time', 'onpaper', 
                                           'tilt1', 'tilt2', 'pressure'])
    return alt_plot(to_plot)
    
    
def alt_plot(to_plot):
    interval = alt.selection_interval()
    return alt.Chart(to_plot.reset_index()).mark_circle().encode(
        x= alt.X('x', scale=alt.Scale(domain=[-10, 60])),
        y= alt.Y('y', scale=alt.Scale(domain=[-10, 60])),
        color='pressure'    #alt.condition(interval, 'onpaper',
                            #alt.value('lightgray'))
    ).add_params(
        interval
    ).interactive()

In [3]:
from ipywidgets import interact

interact(plot_drawing, x=svc_single[(svc_single.DYS == 1)
                                & (svc_single.tsk == '10')
                                & (svc_single.age == 10)].fileindex)

NameError: name 'plot_drawing' is not defined

In [2]:
interact(plot_drawing, x=svc_single[(svc_single.DYS == 0)
                                & (svc_single.tsk == '10')
                                & (svc_single.age == 10)].fileindex)

NameError: name 'interact' is not defined

In [38]:
svc_single[(svc_single.DYS == 0)
        & (svc_single.tsk == '11')
        & (svc_single.age == 8)]

filename tsk  fileindex new_class  age  sex  DYS
1      BH1201  11          1         2  8.0  1.0  0.0
11     BH1203  11         21         2  8.0  2.0  0.0
121    BR1210  11        211         2  8.0  2.0  0.0
131    BR1215  11        261         2  8.0  2.0  0.0
141    BR1217  11        281         2  8.0  1.0  0.0
151    BR1218  11        291         2  8.0  2.0  0.0
161    BR1221  11        321         2  8.0  2.0  0.0
191    BR1325  11        381         3  8.0  1.0  0.0
311    BR3102  11        511         1  8.0  2.0  0.0
331    BR3302  11        611         3  8.0  2.0  0.0
361    BR4205  11        800         2  8.0  2.0  0.0
371    BR4207  11        820         2  8.0  1.0  0.0
381    BR4209  11        840         2  8.0  1.0  0.0
391    BR4211  11        860         2  8.0  2.0  0.0
401    BR4213  11        880         2  8.0  2.0  0.0
411    BR4217  11        920         2  8.0  1.0  0.0
421    BR4220  11        950         2  8.0  1.0  0.0
431    BR4221  11        960         2  8.0  2.0  0.0
441    BR4223  11        980         2  8.0  2.0  0.0
761    BR5106  11       1570         1  8.0  1.0  0.0
771    BR5202  11       1620         2  8.0  1.0  0.0
781    BR5204  11       1640         2  8.0  1.0  0.0
791    BR5205  11       1650         2  8.0  2.0  0.0
837    BR5306  11       1726         3  8.0  1.0  0.0
927    BR7207  11       2076         2  8.0  1.0  0.0
937    BR7209  11       2096         2  8.0  1.0  0.0
947    BR7210  11       2106         2  8.0  1.0  0.0
1007   BR8201  11       2186         2  8.0  1.0  0.0
1017   BR8203  11       2206         2  8.0  1.0  0.0
1027   BR8206  11       2236         2  8.0  2.0  0.0
1037   BR8301  11       2256         3  8.0  1.0  0.0
1047   BR8302  11       2266         3  8.0  1.0  0.0
1067   BR8304  11       2286         3  8.0  2.0  0.0
1127   HK1102  11       3893         1  8.0  2.0  0.0
1137   HK1103  11       3903         1  8.0  1.0  0.0
1147   HK1105  11       3923         1  8.0  2.0  0.0
1157   HK1107  11       3943         1  8.0  2.0  0.0
1457   HK6203  11       4478         2  8.0  1.0  0.0
1507   HK7201  11       4648         2  8.0  2.0  0.0
1517   HK7202  11       4658         2  8.0  1.0  0.0
1527   HK7204  11       4678         2  8.0  1.0  0.0
1537   HK7205  11       4688         2  8.0  1.0  0.0
1547   HK7206  11       4698         2  8.0  2.0  0.0
1557   HK7207  11       4708         2  8.0  1.0  0.0
1567   HK7209  11       4728         2  8.0  2.0  0.0
1577   HK7210  11       4738         2  8.0  2.0  0.0
1627   HK7305  11       4788         3  8.0  2.0  0.0
1667   HK7311  11       4848         3  8.0  2.0  0.0

interact(plot_drawing, x=svc_single[(svc_single.DYS == 0)
                                & (svc_single.tsk == '11')
                                & (svc_single.age == 5)].fileindex);

### Data extraction for visualization
##### and as a simple benchmark for resampling efficiency and quality

In [39]:
svc_single.describe()

fileindex          DYS
count  1686.000000  1686.000000
mean   2234.655397     0.151839
std    1621.382575     0.358971
min       0.000000     0.000000
25%     950.250000     0.000000
50%    1731.500000     0.000000
75%    4049.750000     0.000000
max    4916.000000     1.000000

In [40]:
def acc(series):
    diff = series[1:, :2] - series[:-1, :2]
    return np.concatenate([diff, series[1:, 2:]], axis=1)

In [41]:
def extract(series, i):
    total_time = series[-1, 2] - series[0, 2]
    diff = series[1:] - series[:-1]
    times_touched = np.sum(abs(diff[: 2]))//2
    
    sampling_diff = pd.DataFrame([*diff[:, 2]]).describe().T
    df = pd.DataFrame([*abs(series)], columns=['x', 'y', 'time', 'on_paper', 
                                       'tilt1', 'tilt2', 'pressure'])
    extr_3 = df.describe().T
    #on_paper_extr = df[df.on_paper == 1].describe().T
    off_paper_extr = df[df.on_paper == 0].describe().T
    
    return np.concatenate([[total_time, times_touched, i], sampling_diff,
                          extr_3, off_paper_extr], axis=None)

In [42]:
description = pd.DataFrame(['count', 'mean', 'std', 'min', '25%', '50%', '75%', 'max'])
series_inputs = pd.DataFrame(['x', 'y', 'time', 'on_paper', 'tilt1', 'tilt2', 'pressure'])
states = pd.DataFrame(['combined', 'off_paper'])
writing = list(states.merge(series_inputs.merge(description, how='cross'), how='cross').agg('_'.join, axis=1))
sampl_diff = list(pd.DataFrame(['sampling_diff']).merge(description, how='cross').agg('_'.join, axis=1))
col_names = ['time', 'times_touched', 'fileindex'] + sampl_diff + writing

In [43]:
svc_acc = np.array([acc(series) for series in svc_data], dtype=object)
extracted = np.array([extract(series, i) for i, series in enumerate(svc_acc)])

extracted_df = pd.DataFrame(extracted, columns=col_names)
extracted_df.describe().T

count         mean          std        min  \
time                    5037.0    22.540301    28.706361   0.737000   
times_touched           5037.0    27.868771    23.841957   0.000000   
fileindex               5037.0  2518.000000  1454.200983   0.000000   
sampling_diff_count     5037.0  2448.922176  3148.394312  56.000000   
sampling_diff_mean      5037.0     0.009800     0.006202   0.007514   
...                        ...          ...          ...        ...   
off_paper_pressure_min  4995.0     0.000000     0.000000   0.000000   
off_paper_pressure_25%  4995.0     0.000000     0.000000   0.000000   
off_paper_pressure_50%  4995.0     0.000000     0.000000   0.000000   
off_paper_pressure_75%  4995.0     0.000000     0.000000   0.000000   
off_paper_pressure_max  4995.0     0.000000     0.000000   0.000000   

                                25%          50%         75%           max  
time                       9.358000    14.918000    25.13200    560.804000  
times_touched             12.000000    22.000000    38.00000    320.000000  
fileindex               1259.000000  2518.000000  3777.00000   5036.000000  
sampling_diff_count     1037.000000  1639.000000  2743.00000  50620.000000  
sampling_diff_mean         0.007786     0.008256     0.00955      0.139223  
...                             ...          ...         ...           ...  
off_paper_pressure_min     0.000000     0.000000     0.00000      0.000000  
off_paper_pressure_25%     0.000000     0.000000     0.00000      0.000000  
off_paper_pressure_50%     0.000000     0.000000     0.00000      0.000000  
off_paper_pressure_75%     0.000000     0.000000     0.00000      0.000000  
off_paper_pressure_max     0.000000     0.000000     0.00000      0.000000  

[123 rows x 8 columns]

In [44]:
extracted_df[extracted_df.time < 4]

time  times_touched  fileindex  sampling_diff_count  \
123   3.591           88.0      123.0                308.0   
129   3.370           28.0      129.0                326.0   
135   1.188           26.0      135.0                116.0   
363   2.740           63.0      363.0                357.0   
409   3.211           42.0      409.0                377.0   
449   3.985           60.0      449.0                458.0   
492   3.710            7.0      492.0                485.0   
684   1.571           21.0      684.0                209.0   
838   3.897           23.0      838.0                505.0   
912   3.924            6.0      912.0                522.0   
1272  3.967           16.0     1272.0                495.0   
1292  3.427           33.0     1292.0                450.0   
1468  3.951           72.0     1468.0                507.0   
1610  1.150           48.0     1610.0                120.0   
1715  3.631           50.0     1715.0                471.0   
1718  3.836           49.0     1718.0                502.0   
1724  3.869           94.0     1724.0                505.0   
1767  3.921           15.0     1767.0                483.0   
1834  3.304           75.0     1834.0                354.0   
1894  3.667           57.0     1894.0                454.0   
2018  3.357           27.0     2018.0                427.0   
2264  3.156           64.0     2264.0                408.0   
2318  3.595           86.0     2318.0                467.0   
3093  2.752            4.0     3093.0                361.0   
3198  1.684            6.0     3198.0                224.0   
3443  2.826           40.0     3443.0                376.0   
3445  0.767           15.0     3445.0                102.0   
3447  1.315            8.0     3447.0                175.0   
3449  1.984            0.0     3449.0                264.0   
3453  1.376           10.0     3453.0                183.0   
3523  2.668           10.0     3523.0                355.0   
3557  2.202           36.0     3557.0                293.0   
3615  3.813           65.0     3615.0                501.0   
3763  0.737           15.0     3763.0                 98.0   
3765  1.315            8.0     3765.0                175.0   
3767  1.984            0.0     3767.0                264.0   
3771  1.376           10.0     3771.0                183.0   
3905  3.770            6.0     3905.0                492.0   
3911  3.337           60.0     3911.0                417.0   
3973  3.271           16.0     3973.0                427.0   
3974  3.212           16.0     3974.0                422.0   
3975  2.809           11.0     3975.0                369.0   
4114  3.140           19.0     4114.0                412.0   
4115  2.277            4.0     4115.0                299.0   
4135  3.716           21.0     4135.0                489.0   
4141  3.504           37.0     4141.0                459.0   
4193  3.272            5.0     4193.0                429.0   
4202  3.231            4.0     4202.0                425.0   
4342  3.962           25.0     4342.0                517.0   
4348  3.433            4.0     4348.0                439.0   
4378  3.896            9.0     4378.0                510.0   
4526  3.729           23.0     4526.0                342.0   

      sampling_diff_mean  sampling_diff_std  sampling_diff_min  \
123             0.011659           0.004634              0.007   
129             0.010337           0.004893              0.007   
135             0.010241           0.003661              0.007   
363             0.007675           0.003083              0.007   
409             0.008517           0.007030              0.007   
449             0.008701           0.004088              0.007   
492             0.007649           0.002306              0.007   
684             0.007517           0.000501              0.007   
838             0.007717           0.003417              0.007   
912             0.007517           0.000500              0.0

Notably the tablet sampling (sampling_diff_min) is sometimes very inconsistent, thus, since were considering resampling or interpolating, it will be neccesarry to exclude the empty space (and indeed the difference in movement would make little sense, since there is a major gap between some two neigbouring sampling times). 

In [45]:
extracted_df[(extracted_df.sampling_diff_mean > 0.01) & (extracted_df.sampling_diff_min > 0.1)]

Empty DataFrame
Columns: [time, times_touched, fileindex, sampling_diff_count, sampling_diff_mean, sampling_diff_std, sampling_diff_min, sampling_diff_25%, sampling_diff_50%, sampling_diff_75%, sampling_diff_max, combined_x_count, combined_x_mean, combined_x_std, combined_x_min, combined_x_25%, combined_x_50%, combined_x_75%, combined_x_max, combined_y_count, combined_y_mean, combined_y_std, combined_y_min, combined_y_25%, combined_y_50%, combined_y_75%, combined_y_max, combined_time_count, combined_time_mean, combined_time_std, combined_time_min, combined_time_25%, combined_time_50%, combined_time_75%, combined_time_max, combined_on_paper_count, combined_on_paper_mean, combined_on_paper_std, combined_on_paper_min, combined_on_paper_25%, combined_on_paper_50%, combined_on_paper_75%, combined_on_paper_max, combined_tilt1_count, combined_tilt1_mean, combined_tilt1_std, combined_tilt1_min, combined_tilt1_25%, combined_tilt1_50%, combined_tilt1_75%, combined_tilt1_max, combined_tilt2_count, combined_tilt2_mean, combined_tilt2_std, combined_tilt2_min, combined_tilt2_25%, combined_tilt2_50%, combined_tilt2_75%, combined_tilt2_max, combined_pressure_count, combined_pressure_mean, combined_pressure_std, combined_pressure_min, combined_pressure_25%, combined_pressure_50%, combined_pressure_75%, combined_pressure_max, off_paper_x_count, off_paper_x_mean, off_paper_x_std, off_paper_x_min, off_paper_x_25%, off_paper_x_50%, off_paper_x_75%, off_paper_x_max, off_paper_y_count, off_paper_y_mean, off_paper_y_std, off_paper_y_min, off_paper_y_25%, off_paper_y_50%, off_paper_y_75%, off_paper_y_max, off_paper_time_count, off_paper_time_mean, off_paper_time_std, off_paper_time_min, off_paper_time_25%, off_paper_time_50%, off_paper_time_75%, off_paper_time_max, off_paper_on_paper_count, off_paper_on_paper_mean, off_paper_on_paper_std, off_paper_on_paper_min, off_paper_on_paper_25%, off_paper_on_paper_50%, off_paper_on_paper_75%, off_paper_on_paper_max, off_paper_tilt1_count, ...]
Index: []

[0 rows x 123 columns]

In [46]:
data_extracted = svc_single.merge(extracted_df, how='inner', on='fileindex')
sns.histplot(data_extracted[data_extracted.times_touched < 150],
              hue='DYS', x='times_touched');

NameError: name 'sns' is not defined

## Preprocessing

##### Dealing with the gaps in the sampling

As shown in the previous section there seems to be large gaps between some sampling times (>1s) which would make the resampling very inefficient. To combat this we will split the sample on samling differences larger than 0.1 s.

In [47]:
def split_on_gaps(series):
    diff = series[1:, 2] - series[:-1, 2]
    return np.split(series, np.where(diff > 0.1)[0] + 1) # +1 to offset indexes

##### Resampling the data 

Resampling is done to additionally combat the innacuracies in the original sampling.

In [48]:
from scipy import signal

def resample_series(series, freq=20):
    total_time = series[-1, 2]
    samples = series.shape[0]
    up = max(1, int(np.floor(freq*total_time)))
    return signal.resample_poly(series, up, samples)[4:-4]

Note: removing points on both ends of the approximation since fft tends to be innacurate there.

In [49]:
alt_plot(pd.DataFrame(svc_data[53], columns=['x', 'y', 'time', 'onpaper', 
                           'tilt1', 'tilt2', 'pressure']))

alt.Chart(...)

In [50]:
alt_plot(pd.DataFrame(resample_series(svc_data[53], 40),
                      columns=['x', 'y', 'time', 'onpaper',
                               'tilt1', 'tilt2', 'pressure']))

alt.Chart(...)

The resampling uses a low-pass filter. Also given the nature of the aproximation method (fft) it tends to hallucinate some points otherwise it seems fairly accurate.

##### Splitting the series into windows

The network needs inputs with fixed length, thus it is necessary to split the series. The final length is to be determined, but 120 timesteps (6 seconds with frequency 20/s) is a starting point taken from previous studies.

In [51]:
def series_split(series, total_length, min_length):
    excess = series.shape[0] % total_length 
    
    padding = np.concatenate([[np.zeros(7)]*(total_length - excess),
                              series], axis=0)
    splits = np.array(np.split(padding, padding.shape[0] // total_length))
    splits = splits if excess >= min_length else splits[1:]
    return splits if len(splits) > 0 else np.array([]).reshape((0, 120, 7))